In [1]:
#Ka.<ta> = FunctionField(QQ)
#Kab.<tb> = FunctionField(Ka)
#Kabc.<tc> = FunctionField(Kab)
#Kabcd.<td> = FunctionField(Kabc)
#KK = Kabcd

def E(i, j):
    m = zero_matrix(QQ, 7)
    m[i, j] = 1
    return m

lb = {
    'Xa': E(6, 1) + E(5, 3),
    'Ya': E(1, 6) + E(3, 5),
    'Xa+b': E(5, 0) + E(0, 1)*(-2) + E(6, 2) - E(4, 3),
    'X2a+3b': E(4, 1) + E(5, 2),
    'Xa+2b': E(4, 0) - E(3, 1) + 2* E(0, 2) - E(5, 6),
    'Xa+3b': E(3, 2) - E(4, 6),
    'Xb': E(3, 0) + E(1, 2) + E(4, 5) + 2* E(0, 6),
    'Yb': E(6, 0) + E(2, 1) + 2* E(0, 3) + E(5, 4),
    'Ya+b': E(1, 0) + E(3, 4) + E(0, 5)* (-2) - E(2, 6),
    'Y2a+3b': E(1, 4) + E(2, 5),
    'Ya+2b': E(2, 0) - E(1, 3) + 2* E(0, 4) - E(6, 5),
    'Ya+3b': - E(2, 3) + E(6, 4),
    'Ha': - E(1, 1) - E(3, 3) + E(5, 5) + E(6, 6),
    'Hb': E(1, 1) - E(2, 2) + 2* E(3, 3) + E(4, 4) - E(5, 5) - 2* E(6, 6),
}

def br(x, y):
    return lb[x] * lb[y] - lb[y] * lb[x]

def brbr(x,y,z):
    yz = br(y,z)
    return lb[x] * yz - yz * lb[x]

def comp(A, B):
    for i in range(0, 7):
        for j in range(0, 7):
            if A[i, j] != B[i, j]:
                return False
    return True

def pm_gl2(M):
    return matrix(QQ, [[0, 1], [-1, 0]]) * M * matrix(QQ, [[0, 1], [-1, 0]]).inverse()

def aut_gl2(M):
    return matrix(QQ, [[0, 1], [-1, 0]]) * M.inverse().transpose() * matrix(QQ, [[0, 1], [-1, 0]]).inverse()

def adj(g, X):
    mat = identity_matrix(QQ, 7)
    mat *= (g.inverse() * X * g)
    return mat

unipotents = [lb['Xa'], lb['Xa+b'], lb['Xa+2b'], lb['Xa+3b'], lb['X2a+3b']]
lie_u = gap.VectorSpace(QQ, unipotents)
lie_u_basis = gap.Basis(lie_u, unipotents)

def force(m):
    n = 7
    mat = zero_matrix(QQ, n)
    for i in range(0, n):
        for j in range(0, n):
            mat[i,j]=m[i,j]
    return mat

def adj_matrix(g):
    rows = []
    for x in unipotents:
        m_raw = adj(levi(g), force(x))
        m = force(m_raw)
        if not (m in lie_u):
            print('FFF')
        rows.append(gap.Coefficients(lie_u_basis, m))
    return matrix(QQ, rows)

def adj_matrix_mod(g):
    mat = adj_matrix(g)
    print(mat.determinant())
    return mat*g.determinant()*g.determinant()

def combine_mat(d, pair_list):
    mat = identity_matrix(QQ, d)
    for pr in pair_list:
        ar = pr[1]
        m = pr[0]
        for i in range(0, len(ar)):
            for j in range(0, len(ar)):
                mat[ar[i],ar[j]] = m[i,j]
    return force(mat)

def f2to3(m):
    a=m[0,0]
    b=m[0,1]
    c=m[1,0]
    d=m[1,1]
    return matrix(QQ, [[a*a,a*b,b*b],[2*a*c,a*d+c*b,2*b*d],[c*c,c*d,d*d]])

def f2to4(m):
    a=m[0,0]
    b=m[0,1]
    c=m[1,0]
    d=m[1,1]
    P = matrix(QQ, [[1,0,0,0],[0,1,0,0],[0,0,-1,0],[0,0,0,1]])
    return P*matrix(QQ, [[a*a*a,a*a*b,a*b*b,b*b*b],[3*a*a*c,a*a*d+2*a*c*b,2*a*b*d+b*b*c,3*b*b*d],
                       [3*a*c*c,2*a*c*d+b*c*c,2*b*c*d+a*d*d,3*b*d*d], [c*c*c,c*c*d,c*d*d,d*d*d]])*P.inverse()

def is_the_same(X, Y):
    for it in (X - Y).list():
        if it != 0:
            return False
    return True
    

def levi(m):
    return combine_mat(7, [[f2to3(m), [3, 0, 6]], [m, [1, 2]], [m.determinant()*(m), [4,5]]])

In [58]:
def perm2mat(pe, minus = []):
    m = copy(zero_matrix(QQ, 7))
    for i in range(1, 8):
        m[i-1,pe[i]-1] = -1 if i in minus else 1
    return m

cartan_perm = {1:1, 2:6, 3:5, 4:7, 5:3, 6:2, 7:4}

def tau_c(m):
    pm = perm2mat(cartan_perm, [2,3,5,6])
    return -pm * m * pm

In [61]:
for lbl in lb:
    dct = {'X': 'Y', 'Y': 'X', 'H':'H'}
    lbl2 = dct[lbl[0]] + lbl[1:]
    #if lbl[0] == 'H':
    #    continue
    if not (is_the_same(tau_c(lb[lbl]), lb[lbl2])):
        print(lbl)
        print(tau_c(lb[lbl]))
        print(lbl2)
        print(lb[lbl2])

X2a+3b
[ 0  0  0  0  0  0  0]
[ 0  0  0  0 -1  0  0]
[ 0  0  0  0  0 -1  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
Y2a+3b
[0 0 0 0 0 0 0]
[0 0 0 0 1 0 0]
[0 0 0 0 0 1 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
Xb
[ 0  0  0 -2  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0 -1  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0 -1  0  0]
[-1  0  0  0  0  0  0]
Yb
[0 0 0 2 0 0 0]
[0 0 0 0 0 0 0]
[0 1 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 1 0 0]
[1 0 0 0 0 0 0]
Yb
[ 0  0  0  0  0  0 -2]
[ 0  0 -1  0  0  0  0]
[ 0  0  0  0  0  0  0]
[-1  0  0  0  0  0  0]
[ 0  0  0  0  0 -1  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
Xb
[0 0 0 0 0 0 2]
[0 0 1 0 0 0 0]
[0 0 0 0 0 0 0]
[1 0 0 0 0 0 0]
[0 0 0 0 0 1 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
Y2a+3b
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0]
[ 0 -1  0  0  0  0  0]
[ 0  0 -1  0  0  0  0]
[ 0  0  0 

In [2]:
lb['Ya']**2

[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]

In [51]:
exp(br('Y2a+3b', 'X2a+3b'))

[     1      0      0      0      0      0      0]
[     0      e      0      0      0      0      0]
[     0      0      e      0      0      0      0]
[     0      0      0      1      0      0      0]
[     0      0      0      0 e^(-1)      0      0]
[     0      0      0      0      0 e^(-1)      0]
[     0      0      0      0      0      0      1]

In [4]:
lb['Xa']**2

[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]

In [10]:
lb['X2a+3b']**3

[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]
[0 0 0 0 0 0 0]